In [1]:
from human_aware_rl.utils import set_style
from human_aware_rl.experiments.bc_experiments import *
from human_aware_rl.experiments.pbt_experiments import *
from human_aware_rl.experiments.ppo_bc_experiments import *
from human_aware_rl.experiments.ppo_sp_experiments import *
from human_aware_rl.experiments.planning_experiments import P_BC_evaluation

best_bc_model_paths = load_pickle("data/bc_runs/best_bc_model_paths")
best_bc_models_performance = load_pickle("data/bc_runs/best_bc_models_performance")
set_style()

layouts = ['simple', 'unident_s']
delivery_horizon_dict = {"simple": 2, "unident_s": 3}

from overcooked_ai_py.mdp.overcooked_env import OvercookedEnv
from overcooked_ai_py.agents.benchmarking import AgentEvaluator
from overcooked_ai_py.agents.agent import EmbeddedPlanningAgent, AgentPair

from human_aware_rl.imitation.behavioural_cloning import get_bc_agent_from_saved

import json, copy
import numpy as np

from overcooked_ai_py.utils import save_pickle, load_pickle, cumulative_rewards_from_rew_list, save_as_json, load_from_json
from overcooked_ai_py.planning.planners import NO_COUNTERS_PARAMS, MediumLevelPlanner
from overcooked_ai_py.mdp.layout_generator import LayoutGenerator
from overcooked_ai_py.agents.agent import AgentPair, CoupledPlanningAgent, RandomAgent, GreedyHumanModel, CoupledPlanningExperimentalAgent
from overcooked_ai_py.mdp.overcooked_mdp import OvercookedGridworld, Action, OvercookedState
from overcooked_ai_py.mdp.overcooked_env import OvercookedEnv



best_bc_models = load_pickle("data/bc_runs/best_bc_model_paths")

set_global_seed(166)

/home/nils/miniconda3/envs/model_conversion/lib/python3.7/site-packages/tensorflow/python/framework/dtypes.py:526: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint8 = np.dtype([("qint8", np.int8, 1)])
/home/nils/miniconda3/envs/model_conversion/lib/python3.7/site-packages/tensorflow/python/framework/dtypes.py:527: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_quint8 = np.dtype([("quint8", np.uint8, 1)])
/home/nils/miniconda3/envs/model_conversion/lib/python3.7/site-packages/tensorflow/python/framework/dtypes.py:528: FutureWarning: Passing (type, 1) or '1type' as a synonym of type is deprecated; in a future version of numpy, it will be understood as (type, (1,)) / '(1,)type'.
  _np_qint16 = np.dtype([("qint16", np.int16, 1)])
/home/nils/minicond

In [2]:
# CP+HPROXY horizon 100
cp_performance = {}
for layout in layouts:
    ae = AgentEvaluator(mdp_params={'layout_name': layout}, env_params={'horizon': 100})
    
    test_model_name = best_bc_models["test"][layout]
    agent_bc_test, _ = get_bc_agent_from_saved(test_model_name)
    agent_bc_test.stochastic = False
    
    a0 = CoupledPlanningExperimentalAgent(ae.mlp)
    agent_pair = AgentPair(a0, agent_bc_test)
    
    traj = ae.evaluate_agent_pair(agent_pair, display=display)
    cp_performance[layout] = traj['ep_returns'][0]

cp_performance

Loading a model without an environment, this model cannot be trained until it has a valid environment.
Instructions for updating:
Colocations handled automatically by placer.
Instructions for updating:
Use keras.layers.flatten instead.
Instructions for updating:
Use tf.cast instead.
Instructions for updating:
Deprecated in favor of operator or tf.math.divide.
Loaded MediumLevelPlanner from /home/nils/human_aware_rl/overcooked_ai/overcooked_ai_py/data/planners/simple_am.pkl
Loaded MediumLevelPlanner from /home/nils/human_aware_rl/overcooked_ai/overcooked_ai_py/data/planners/simple_am.pkl


  0%|                                                                                             | 0/1 [00:00<?, ?it/s]

X X P X X 
O     ↑1O 
X ↑0    X 
X D X S X 

Found goal after: 	2.29 seconds,   	7797 state expanded (0.33 unique) 	 ~3400.83 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((3, 1), (1, 0)))
failures:  0
Timestep: 1
Joint action taken: ('↑', 'stay') 	 Reward: 0 + shape * 0 
X X P X X 
O ↑0  ↑1O 
X       X 
X D X S X 


Found goal after: 	2.08 seconds,   	7826 state expanded (0.32 unique) 	 ~3768.64 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 2
Joint action taken: ('←', 'stay') 	 Reward: 0 + shape * 0 
X X P X X 
O ←0  ↑1O 
X       X 
X D X S X 


Found goal after: 	2.31 seconds,   	7776 state expanded (0.33 unique) 	 ~3360.93 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((3, 1), (1, 0)))
failures:  0
Timestep: 3
Joint action taken: ('interact', 'stay') 	 Reward: 0 + shape * 0 
X X P X X 
O ←o  ↑1O 
X       X 
X D X S X 


Found goal after: 	1.98 seconds,   	7591 state expanded (0.32 unique) 	 ~3826.29 expansions/s
First m

Found goal after: 	1.04 seconds,   	3490 state expanded (0.33 unique) 	 ~3367.96 expansions/s
First motion goal:  (((3, 1), (1, 0)), ((1, 2), (0, 1)))
failures:  18
Timestep: 41
Joint action taken: ('interact', '←') 	 Reward: 0 + shape * 0 
X X ø20X X 
O     →oO 
X ←1    X 
X D XoS X 


Found goal after: 	1.02 seconds,   	3482 state expanded (0.33 unique) 	 ~3403.42 expansions/s
First motion goal:  (((3, 1), (1, 0)), ((1, 2), (0, 1)))
failures:  18
Timestep: 42
Joint action taken: ('interact', '↓') 	 Reward: 0 + shape * 0 
X X ø20X X 
O     →oO 
X ↓1    X 
X D XoS X 


Found goal after: 	1.10 seconds,   	3478 state expanded (0.33 unique) 	 ~3168.21 expansions/s
First motion goal:  (((3, 1), (1, 0)), ((1, 2), (0, 1)))
failures:  18
Timestep: 43
Joint action taken: ('interact', 'interact') 	 Reward: 0 + shape * 0 
X X ø20X X 
O     →oO 
X ↓d    X 
X D XoS X 


Found goal after: 	1.09 seconds,   	3461 state expanded (0.33 unique) 	 ~3161.17 expansions/s
First motion goal:  (((3, 1), (1, 0

Found goal after: 	1.66 seconds,   	5664 state expanded (0.33 unique) 	 ~3419.12 expansions/s
First motion goal:  (((1, 2), (0, 1)), ((1, 1), (-1, 0)))
failures:  18
Timestep: 70
Joint action taken: ('←', '↑') 	 Reward: 0 + shape * 0 
X X ø4X X 
O ↑1    O 
X ←0    X 
X D XoS X 


Found goal after: 	1.45 seconds,   	5378 state expanded (0.33 unique) 	 ~3704.69 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((1, 2), (0, 1)))
failures:  18
Timestep: 71
Joint action taken: ('↑', 'stay') 	 Reward: 0 + shape * 0 
X X ø5X X 
O ↑1    O 
X ↑0    X 
X D XoS X 


Found goal after: 	1.63 seconds,   	5317 state expanded (0.33 unique) 	 ~3254.11 expansions/s
First motion goal:  (((1, 2), (0, 1)), ((1, 1), (-1, 0)))
failures:  18
Timestep: 72
Joint action taken: ('↓', 'stay') 	 Reward: 0 + shape * 0 
X X ø6X X 
O ↑1    O 
X ↓0    X 
X D XoS X 


Found goal after: 	1.47 seconds,   	4888 state expanded (0.33 unique) 	 ~3326.94 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((1, 1), (-1, 0))

...

Found goal after: 	6.44 seconds,   	17572 state expanded (0.37 unique) 	 ~2728.55 expansions/s
First motion goal:  (((5, 2), (-1, 0)), ((3, 2), (1, 0)))
failures:  0
Timestep: 50
Joint action taken: ('←', 'stay') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X     ↑oP ←o    X 
X       ø20      X 
X X X D X D X X X 


Found goal after: 	5.38 seconds,   	18626 state expanded (0.37 unique) 	 ~3462.38 expansions/s
First motion goal:  (((5, 2), (-1, 0)), ((3, 2), (1, 0)))
failures:  0
Timestep: 51
Joint action taken: ('interact', '→') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X     →oø-←0    X 
X       ø20      X 
X X X D X D X X X 


Found goal after: 	5.01 seconds,   	18625 state expanded (0.37 unique) 	 ~3717.32 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 2), (1, 0)))
failures:  0
Timestep: 52
Joint action taken: ('↑', 'stay') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X     →oø-↑0    X 
X       ø20      X 
X X X D X

Found goal after: 	6.40 seconds,   	22511 state expanded (0.36 unique) 	 ~3515.02 expansions/s
First motion goal:  (((5, 3), (-1, 0)), ((3, 3), (1, 0)))
failures:  0
Timestep: 75
Joint action taken: ('↓', '↓') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X       ø17      X 
X ↓o    P ↓o    X 
X X X D X D X X X 


Found goal after: 	6.47 seconds,   	22963 state expanded (0.36 unique) 	 ~3547.09 expansions/s
First motion goal:  (((5, 3), (-1, 0)), ((3, 3), (1, 0)))
failures:  0
Timestep: 76
Joint action taken: ('←', '→') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X       ø18      X 
X   →o  P ←o    X 
X X X D X D X X X 


Found goal after: 	6.70 seconds,   	22963 state expanded (0.36 unique) 	 ~3426.80 expansions/s
First motion goal:  (((5, 3), (-1, 0)), ((3, 3), (1, 0)))
failures:  0
Timestep: 77
Joint action taken: ('interact', '→') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X       ø19      X 
X     →oø-←0    X 
X X X D X D X X

100%|████████████████████████████████████████████████████████████████████████████████████| 1/1 [14:07<00:00, 847.16s/it]

Found goal after: 	0.11 seconds,   	308 state expanded (0.49 unique) 	 ~2684.24 expansions/s
First motion goal:  (((5, 3), (-1, 0)), ((3, 3), (1, 0)))
failures:  0
Timestep: 96
Joint action taken: ('interact', '↑') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X     ↑dø20      X 
X       ø15←d    X 
X X X D X D X X X 


Found goal after: 	0.09 seconds,   	211 state expanded (0.56 unique) 	 ~2303.27 expansions/s
First motion goal:  (((5, 2), (-1, 0)), ((3, 3), (1, 0)))
failures:  0
Timestep: 97
Joint action taken: ('↑', '→') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X     →dø20↑d    X 
X       ø16      X 
X X X D X D X X X 


Found goal after: 	0.03 seconds,   	67 state expanded (0.79 unique) 	 ~2107.09 expansions/s
First motion goal:  (((5, 2), (-1, 0)), ((3, 3), (1, 0)))
failures:  0
Timestep: 98
Joint action taken: ('←', 'stay') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X     →dø20←d    X 
X       ø17      X 
X X X D X D X X 

{'simple': 40.0, 'unident_s': 40.0}

In [3]:
# CP+HPROXY switched indices horizon 100
cp_performance = {}
for layout in layouts:
    ae = AgentEvaluator(mdp_params={'layout_name': layout}, env_params={'horizon': 100})
    
    test_model_name = best_bc_models["test"][layout]
    agent_bc_test, _ = get_bc_agent_from_saved(test_model_name)
    agent_bc_test.stochastic = False
    
    a0 = CoupledPlanningExperimentalAgent(ae.mlp)
    agent_pair = AgentPair(agent_bc_test, a0)
    
    traj = ae.evaluate_agent_pair(agent_pair, display=display)
    cp_performance[layout] = traj['ep_returns'][0]

cp_performance

Loading a model without an environment, this model cannot be trained until it has a valid environment.
Loaded MediumLevelPlanner from /home/nils/human_aware_rl/overcooked_ai/overcooked_ai_py/data/planners/simple_am.pkl
Loaded MediumLevelPlanner from /home/nils/human_aware_rl/overcooked_ai/overcooked_ai_py/data/planners/simple_am.pkl


  0%|                                                                                             | 0/1 [00:00<?, ?it/s]

X X P X X 
O     ↑1O 
X ↑0    X 
X D X S X 

Found goal after: 	2.65 seconds,   	7797 state expanded (0.33 unique) 	 ~2945.39 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((3, 1), (1, 0)))
failures:  0
Timestep: 1
Joint action taken: ('stay', '→') 	 Reward: 0 + shape * 0 
X X P X X 
O     →1O 
X ↑0    X 
X D X S X 


Found goal after: 	4.34 seconds,   	7842 state expanded (0.32 unique) 	 ~1805.10 expansions/s
First motion goal:  (((1, 2), (0, 1)), ((3, 1), (1, 0)))
failures:  0
Timestep: 2
Joint action taken: ('stay', 'interact') 	 Reward: 0 + shape * 0 
X X P X X 
O     →oO 
X ↑0    X 
X D X S X 


Found goal after: 	4.26 seconds,   	7612 state expanded (0.32 unique) 	 ~1788.41 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((2, 1), (0, -1)))
failures:  0
Timestep: 3
Joint action taken: ('stay', '←') 	 Reward: 0 + shape * 0 
X X P X X 
O   ←o  O 
X ↑0    X 
X D X S X 


Found goal after: 	3.52 seconds,   	7702 state expanded (0.32 unique) 	 ~2191.02 expansions/s
First mo

Found goal after: 	1.14 seconds,   	3383 state expanded (0.33 unique) 	 ~2955.51 expansions/s
First motion goal:  (((2, 1), (0, -1)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 30
Joint action taken: ('↑', 'interact') 	 Reward: 0 + shape * 0 
X X ø14X X 
O ←o↑d  O 
X       X 
X D X S X 


Found goal after: 	1.09 seconds,   	3381 state expanded (0.33 unique) 	 ~3098.01 expansions/s
First motion goal:  (((2, 1), (0, -1)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 31
Joint action taken: ('stay', 'interact') 	 Reward: 0 + shape * 0 
X X ø15X X 
O ←o↑d  O 
X       X 
X D X S X 


Found goal after: 	1.52 seconds,   	3379 state expanded (0.33 unique) 	 ~2219.67 expansions/s
First motion goal:  (((2, 1), (0, -1)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 32
Joint action taken: ('stay', 'interact') 	 Reward: 0 + shape * 0 
X X ø16X X 
O ←o↑d  O 
X       X 
X D X S X 


Found goal after: 	1.39 seconds,   	3377 state expanded (0.33 unique) 	 ~2421.34 expansions/s
First motion goal:  (((2, 1), (0,

Found goal after: 	3.04 seconds,   	5617 state expanded (0.33 unique) 	 ~1847.44 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((1, 2), (0, 1)))
failures:  0
Timestep: 59
Joint action taken: ('stay', '→') 	 Reward: 0 + shape * 0 
X X ø3X X 
O   →1  O 
X ←0    X 
X D X S X 


Found goal after: 	1.61 seconds,   	5261 state expanded (0.33 unique) 	 ~3262.12 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((1, 2), (0, 1)))
failures:  0
Timestep: 60
Joint action taken: ('interact', '↓') 	 Reward: 0 + shape * 0 
X X ø4X X 
O       O 
X ←0↓1  X 
X D X S X 


Found goal after: 	1.76 seconds,   	5188 state expanded (0.33 unique) 	 ~2953.14 expansions/s
First motion goal:  (((1, 2), (0, 1)), ((3, 1), (1, 0)))
failures:  0
Timestep: 61
Joint action taken: ('↓', '↑') 	 Reward: 0 + shape * 0 
X X ø5X X 
O   ↑1  O 
X ↓0    X 
X D X S X 


Found goal after: 	1.80 seconds,   	5353 state expanded (0.33 unique) 	 ~2976.06 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((1, 2), (0, 1)))

...

Found goal after: 	0.87 seconds,   	3852 state expanded (0.37 unique) 	 ~4411.40 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 2), (1, 0)))
failures:  0
Timestep: 50
Joint action taken: ('interact', '→') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X     →dø6      X 
X       ø20↓d    X 
X X X D X D X X X 


Found goal after: 	0.44 seconds,   	2015 state expanded (0.35 unique) 	 ~4542.00 expansions/s
First motion goal:  (((5, 2), (-1, 0)), ((3, 2), (1, 0)))
failures:  0
Timestep: 51
Joint action taken: ('↑', 'interact') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X     →dø7↑d    X 
X       ø20      X 
X X X D X D X X X 


Found goal after: 	0.37 seconds,   	1716 state expanded (0.36 unique) 	 ~4590.24 expansions/s
First motion goal:  (((5, 2), (-1, 0)), ((3, 2), (1, 0)))
failures:  0
Timestep: 52
Joint action taken: ('stay', 'interact') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X     →dø8↑d    X 
X       ø20      X 
X

Found goal after: 	27.39 seconds,   	87961 state expanded (0.35 unique) 	 ~3211.80 expansions/s
First motion goal:  (((7, 1), (1, 0)), ((3, 2), (1, 0)))
failures:  0
Timestep: 75
Joint action taken: ('→', 'interact') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X     →1ø-    →sX 
X       P       X 
X X X D X D X X X 


Found goal after: 	13.02 seconds,   	44530 state expanded (0.35 unique) 	 ~3419.31 expansions/s
First motion goal:  (((7, 1), (1, 0)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 76
Joint action taken: ('↑', '←') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X ↑sS 
X   ←1  ø-      X 
X       P       X 
X X X D X D X X X 


Found goal after: 	16.78 seconds,   	47192 state expanded (0.35 unique) 	 ~2811.74 expansions/s
First motion goal:  (((7, 1), (1, 0)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 77
Joint action taken: ('→', '←') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X →sS 
X ←1    ø-      X 
X       P       X 
X X X D X D X X 

100%|███████████████████████████████████████████████████████████████████████████████████| 1/1 [31:58<00:00, 1918.97s/it]

Found goal after: 	16.46 seconds,   	43723 state expanded (0.33 unique) 	 ~2656.11 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 3), (1, 0)))
failures:  0
Timestep: 100
Joint action taken: ('interact', '↓') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X       ø=↑o    X 
X     ↓oø-      X 
X X X D X D X X X 


Avg reward 40.00 (std: 0.00, se: 0.00) over 1 games of avg length 100.0


{'simple': 40.0, 'unident_s': 40.0}

In [4]:
# CP+HPROXY horizon 400
cp_performance = {}
for layout in layouts:
    ae = AgentEvaluator(mdp_params={'layout_name': layout}, env_params={'horizon': 400})
    
    test_model_name = best_bc_models["test"][layout]
    agent_bc_test, _ = get_bc_agent_from_saved(test_model_name)
    agent_bc_test.stochastic = False
    
    a0 = CoupledPlanningExperimentalAgent(ae.mlp)
    agent_pair = AgentPair(a0, agent_bc_test)
    
    traj = ae.evaluate_agent_pair(agent_pair, display=display)
    cp_performance[layout] = traj['ep_returns'][0]

cp_performance

Loading a model without an environment, this model cannot be trained until it has a valid environment.
Loaded MediumLevelPlanner from /home/nils/human_aware_rl/overcooked_ai/overcooked_ai_py/data/planners/simple_am.pkl
Loaded MediumLevelPlanner from /home/nils/human_aware_rl/overcooked_ai/overcooked_ai_py/data/planners/simple_am.pkl


  0%|                                                                                             | 0/1 [00:00<?, ?it/s]

X X P X X 
O     ↑1O 
X ↑0    X 
X D X S X 

Found goal after: 	4.20 seconds,   	7797 state expanded (0.33 unique) 	 ~1855.95 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((3, 1), (1, 0)))
failures:  0
Timestep: 1
Joint action taken: ('↑', 'stay') 	 Reward: 0 + shape * 0 
X X P X X 
O ↑0  ↑1O 
X       X 
X D X S X 


Found goal after: 	4.47 seconds,   	7826 state expanded (0.32 unique) 	 ~1751.33 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 2
Joint action taken: ('←', 'stay') 	 Reward: 0 + shape * 0 
X X P X X 
O ←0  ↑1O 
X       X 
X D X S X 


Found goal after: 	3.19 seconds,   	7776 state expanded (0.33 unique) 	 ~2434.36 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((3, 1), (1, 0)))
failures:  0
Timestep: 3
Joint action taken: ('interact', 'stay') 	 Reward: 0 + shape * 0 
X X P X X 
O ←o  ↑1O 
X       X 
X D X S X 


Found goal after: 	2.37 seconds,   	7591 state expanded (0.32 unique) 	 ~3198.91 expansions/s
First m

Found goal after: 	1.04 seconds,   	3490 state expanded (0.33 unique) 	 ~3356.93 expansions/s
First motion goal:  (((3, 1), (1, 0)), ((1, 2), (0, 1)))
failures:  18
Timestep: 41
Joint action taken: ('interact', '←') 	 Reward: 0 + shape * 0 
X X ø20X X 
O     →oO 
X ←1    X 
X D XoS X 


Found goal after: 	1.15 seconds,   	3482 state expanded (0.33 unique) 	 ~3037.62 expansions/s
First motion goal:  (((3, 1), (1, 0)), ((1, 2), (0, 1)))
failures:  18
Timestep: 42
Joint action taken: ('interact', '↓') 	 Reward: 0 + shape * 0 
X X ø20X X 
O     →oO 
X ↓1    X 
X D XoS X 


Found goal after: 	1.04 seconds,   	3478 state expanded (0.33 unique) 	 ~3354.75 expansions/s
First motion goal:  (((3, 1), (1, 0)), ((1, 2), (0, 1)))
failures:  18
Timestep: 43
Joint action taken: ('interact', 'interact') 	 Reward: 0 + shape * 0 
X X ø20X X 
O     →oO 
X ↓d    X 
X D XoS X 


Found goal after: 	1.04 seconds,   	3461 state expanded (0.33 unique) 	 ~3330.59 expansions/s
First motion goal:  (((3, 1), (1, 0

Found goal after: 	1.58 seconds,   	5664 state expanded (0.33 unique) 	 ~3577.49 expansions/s
First motion goal:  (((1, 2), (0, 1)), ((1, 1), (-1, 0)))
failures:  18
Timestep: 70
Joint action taken: ('←', '↑') 	 Reward: 0 + shape * 0 
X X ø4X X 
O ↑1    O 
X ←0    X 
X D XoS X 


Found goal after: 	1.61 seconds,   	5378 state expanded (0.33 unique) 	 ~3348.22 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((1, 2), (0, 1)))
failures:  18
Timestep: 71
Joint action taken: ('↑', 'stay') 	 Reward: 0 + shape * 0 
X X ø5X X 
O ↑1    O 
X ↑0    X 
X D XoS X 


Found goal after: 	1.51 seconds,   	5317 state expanded (0.33 unique) 	 ~3519.30 expansions/s
First motion goal:  (((1, 2), (0, 1)), ((1, 1), (-1, 0)))
failures:  18
Timestep: 72
Joint action taken: ('↓', 'stay') 	 Reward: 0 + shape * 0 
X X ø6X X 
O ↑1    O 
X ↓0    X 
X D XoS X 


Found goal after: 	1.36 seconds,   	4888 state expanded (0.33 unique) 	 ~3583.17 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((1, 1), (-1, 0))

...

Found goal after: 	7.70 seconds,   	34972 state expanded (0.36 unique) 	 ~4539.30 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 2), (1, 0)))
failures:  0
Timestep: 360
Joint action taken: ('interact', 'stay') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
Xd      ø=↑o    X 
X     →dø20      X 
X X X D X D X X X 


Found goal after: 	6.33 seconds,   	28521 state expanded (0.37 unique) 	 ~4507.01 expansions/s
First motion goal:  (((5, 2), (-1, 0)), ((3, 3), (1, 0)))
failures:  0
Timestep: 361
Joint action taken: ('←', 'stay') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
Xd      ø=←o    X 
X     →dø20      X 
X X X D X D X X X 


Found goal after: 	1.98 seconds,   	10200 state expanded (0.35 unique) 	 ~5150.74 expansions/s
First motion goal:  (((5, 2), (-1, 0)), ((3, 2), (1, 0)))
failures:  0
Timestep: 362
Joint action taken: ('interact', 'interact') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
Xd      ø1←0    X 
X     →sP   

Found goal after: 	0.30 seconds,   	1578 state expanded (0.40 unique) 	 ~5225.23 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 2), (1, 0)))
failures:  0
Timestep: 385
Joint action taken: ('interact', 'stay') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
Xd      ø20↑o    X 
X     ↓dø7      X 
X X X D X D X X X 


Found goal after: 	0.21 seconds,   	1135 state expanded (0.42 unique) 	 ~5326.32 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 2), (1, 0)))
failures:  0
Timestep: 386
Joint action taken: ('interact', '→') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
Xd      ø20↑o    X 
X     →dø8      X 
X X X D X D X X X 


Found goal after: 	0.19 seconds,   	789 state expanded (0.43 unique) 	 ~4097.65 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 2), (1, 0)))
failures:  0
Timestep: 387
Joint action taken: ('interact', 'stay') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
Xd      ø20↑o    X 
X     →dø9     

100%|███████████████████████████████████████████████████████████████████████████████████| 1/1 [36:40<00:00, 2200.63s/it]

Timestep: 392
Joint action taken: ('interact', '↑') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
Xd    ↑dø20↑o    X 
X       ø14      X 
X X X D X D X X X 


Found goal after: 	0.03 seconds,   	102 state expanded (0.55 unique) 	 ~3991.07 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 2), (1, 0)))
failures:  0
Timestep: 393
Joint action taken: ('interact', 'stay') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
Xd    ↑dø20↑o    X 
X       ø15      X 
X X X D X D X X X 


Found goal after: 	0.02 seconds,   	90 state expanded (0.58 unique) 	 ~3887.41 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 2), (1, 0)))
failures:  0
Timestep: 394
Joint action taken: ('interact', 'stay') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
Xd    ↑dø20↑o    X 
X       ø16      X 
X X X D X D X X X 


Found goal after: 	0.02 seconds,   	75 state expanded (0.64 unique) 	 ~3590.81 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 2)

{'simple': 180.0, 'unident_s': 280.0}

In [5]:
# CP+HPROXY switched indices horizon 400
cp_performance = {}
for layout in layouts:
    ae = AgentEvaluator(mdp_params={'layout_name': layout}, env_params={'horizon': 400})
    
    test_model_name = best_bc_models["test"][layout]
    agent_bc_test, _ = get_bc_agent_from_saved(test_model_name)
    agent_bc_test.stochastic = False
    
    a0 = CoupledPlanningExperimentalAgent(ae.mlp)
    agent_pair = AgentPair(agent_bc_test, a0)
    
    traj = ae.evaluate_agent_pair(agent_pair, display=display)
    cp_performance[layout] = traj['ep_returns'][0]

cp_performance

Loading a model without an environment, this model cannot be trained until it has a valid environment.
Loaded MediumLevelPlanner from /home/nils/human_aware_rl/overcooked_ai/overcooked_ai_py/data/planners/simple_am.pkl
Loaded MediumLevelPlanner from /home/nils/human_aware_rl/overcooked_ai/overcooked_ai_py/data/planners/simple_am.pkl


  0%|                                                                                             | 0/1 [00:00<?, ?it/s]

X X P X X 
O     ↑1O 
X ↑0    X 
X D X S X 

Found goal after: 	1.65 seconds,   	7797 state expanded (0.33 unique) 	 ~4721.62 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((3, 1), (1, 0)))
failures:  0
Timestep: 1
Joint action taken: ('stay', '→') 	 Reward: 0 + shape * 0 
X X P X X 
O     →1O 
X ↑0    X 
X D X S X 


Found goal after: 	1.67 seconds,   	7842 state expanded (0.32 unique) 	 ~4696.52 expansions/s
First motion goal:  (((1, 2), (0, 1)), ((3, 1), (1, 0)))
failures:  0
Timestep: 2
Joint action taken: ('stay', 'interact') 	 Reward: 0 + shape * 0 
X X P X X 
O     →oO 
X ↑0    X 
X D X S X 


Found goal after: 	1.55 seconds,   	7612 state expanded (0.32 unique) 	 ~4914.13 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((2, 1), (0, -1)))
failures:  0
Timestep: 3
Joint action taken: ('stay', '←') 	 Reward: 0 + shape * 0 
X X P X X 
O   ←o  O 
X ↑0    X 
X D X S X 


Found goal after: 	1.87 seconds,   	7702 state expanded (0.32 unique) 	 ~4108.06 expansions/s
First mo

Found goal after: 	0.77 seconds,   	3383 state expanded (0.33 unique) 	 ~4389.00 expansions/s
First motion goal:  (((2, 1), (0, -1)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 30
Joint action taken: ('↑', 'interact') 	 Reward: 0 + shape * 0 
X X ø14X X 
O ←o↑d  O 
X       X 
X D X S X 


Found goal after: 	0.76 seconds,   	3381 state expanded (0.33 unique) 	 ~4470.76 expansions/s
First motion goal:  (((2, 1), (0, -1)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 31
Joint action taken: ('stay', 'interact') 	 Reward: 0 + shape * 0 
X X ø15X X 
O ←o↑d  O 
X       X 
X D X S X 


Found goal after: 	0.74 seconds,   	3379 state expanded (0.33 unique) 	 ~4568.57 expansions/s
First motion goal:  (((2, 1), (0, -1)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 32
Joint action taken: ('stay', 'interact') 	 Reward: 0 + shape * 0 
X X ø16X X 
O ←o↑d  O 
X       X 
X D X S X 


Found goal after: 	0.73 seconds,   	3377 state expanded (0.33 unique) 	 ~4623.08 expansions/s
First motion goal:  (((2, 1), (0,

Found goal after: 	1.26 seconds,   	5617 state expanded (0.33 unique) 	 ~4463.08 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((1, 2), (0, 1)))
failures:  0
Timestep: 59
Joint action taken: ('stay', '→') 	 Reward: 0 + shape * 0 
X X ø3X X 
O   →1  O 
X ←0    X 
X D X S X 


Found goal after: 	1.04 seconds,   	5261 state expanded (0.33 unique) 	 ~5053.64 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((1, 2), (0, 1)))
failures:  0
Timestep: 60
Joint action taken: ('interact', '↓') 	 Reward: 0 + shape * 0 
X X ø4X X 
O       O 
X ←0↓1  X 
X D X S X 


Found goal after: 	1.24 seconds,   	5188 state expanded (0.33 unique) 	 ~4198.57 expansions/s
First motion goal:  (((1, 2), (0, 1)), ((3, 1), (1, 0)))
failures:  0
Timestep: 61
Joint action taken: ('↓', '↑') 	 Reward: 0 + shape * 0 
X X ø5X X 
O   ↑1  O 
X ↓0    X 
X D X S X 


Found goal after: 	1.15 seconds,   	5353 state expanded (0.33 unique) 	 ~4671.63 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((1, 2), (0, 1)))

...

Found goal after: 	9.07 seconds,   	43723 state expanded (0.33 unique) 	 ~4822.24 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 3), (1, 0)))
failures:  0
Timestep: 368
Joint action taken: ('interact', '↓') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X       ø=↑o    X 
X     ↓oø-      X 
X X X D X D X X X 


Found goal after: 	6.42 seconds,   	34334 state expanded (0.32 unique) 	 ~5348.73 expansions/s
First motion goal:  (((5, 2), (-1, 0)), ((3, 2), (1, 0)))
failures:  0
Timestep: 369
Joint action taken: ('←', '↑') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X     ↑oø=←o    X 
X       ø-      X 
X X X D X D X X X 


Found goal after: 	4.44 seconds,   	21216 state expanded (0.33 unique) 	 ~4783.14 expansions/s
First motion goal:  (((5, 2), (-1, 0)), ((3, 2), (1, 0)))
failures:  0
Timestep: 370
Joint action taken: ('interact', '→') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X     →oø1←0    X 
X       ø-      X 
X X X D 

Found goal after: 	0.41 seconds,   	2389 state expanded (0.39 unique) 	 ~5809.52 expansions/s
First motion goal:  (((5, 3), (-1, 0)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 393
Joint action taken: ('stay', '↑') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X     ↑1ø20↑d    X 
X       ø7      X 
X X X D X D X X X 


Found goal after: 	0.58 seconds,   	1952 state expanded (0.39 unique) 	 ~3365.41 expansions/s
First motion goal:  (((5, 2), (-1, 0)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 394
Joint action taken: ('stay', '←') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X   ←1  ø20↑d    X 
X       ø8      X 
X X X D X D X X X 


Found goal after: 	0.23 seconds,   	1280 state expanded (0.43 unique) 	 ~5637.41 expansions/s
First motion goal:  (((5, 2), (-1, 0)), ((3, 3), (0, 1)))
failures:  0
Timestep: 395
Joint action taken: ('←', '→') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X     →1ø20←d    X 
X       ø9      X 
X X X D X D X 

100%|█████████████████████████████████████████████████████████████████████████████████| 1/1 [1:07:17<00:00, 4037.10s/it]

Found goal after: 	0.13 seconds,   	676 state expanded (0.47 unique) 	 ~5225.93 expansions/s
First motion goal:  (((5, 3), (-1, 0)), ((3, 3), (0, 1)))
failures:  0
Timestep: 398
Joint action taken: ('stay', '↓') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X       ø20←d    X 
X     ↓1ø12      X 
X X X D X D X X X 


Found goal after: 	0.10 seconds,   	492 state expanded (0.51 unique) 	 ~5170.29 expansions/s
First motion goal:  (((5, 2), (-1, 0)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 399
Joint action taken: ('interact', '↑') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X     ↑1P ←s    X 
X       ø13      X 
X X X D X D X X X 


Found goal after: 	0.01 seconds,   	35 state expanded (0.54 unique) 	 ~5182.17 expansions/s
First motion goal:  (((7, 1), (1, 0)), ((3, 3), (0, 1)))
failures:  0
Timestep: 400
Joint action taken: ('→', '↓') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X       P   →s  X 
X     ↓1ø14      X 
X X X D X D X X

{'simple': 160.0, 'unident_s': 200.0}

Conclusions over num_games=1 :

CP + HProxy (BC_TEST)

100 horizon 

simple  40 - failures 18
unidents: 40 - failures 0

400 horizon

simple  :  180 - failures 18
unidents: 280 - failures 0

Switched indices CP + HProxy (BC_TEST)

100 horizon -> extrapolate 400

simple  : 40 - failures 0
unidents: 40 - failures 0

400 horizon

simple  : 160 - failures 0
unidents: 200 - failures 0

In [6]:
# CP+HPROXY horizon 100, 5x
cp_performance = {}
for layout in layouts:
    ae = AgentEvaluator(mdp_params={'layout_name': layout}, env_params={'horizon': 100})
    
    test_model_name = best_bc_models["test"][layout]
    agent_bc_test, _ = get_bc_agent_from_saved(test_model_name)
    agent_bc_test.stochastic = False
    
    a0 = CoupledPlanningExperimentalAgent(ae.mlp)
    agent_pair = AgentPair(a0, agent_bc_test)
    
    traj = ae.evaluate_agent_pair(agent_pair, 5, display=display)
    cp_performance[layout] = traj['ep_returns'][0]

cp_performance

Loading a model without an environment, this model cannot be trained until it has a valid environment.
Loaded MediumLevelPlanner from /home/nils/human_aware_rl/overcooked_ai/overcooked_ai_py/data/planners/simple_am.pkl
Loaded MediumLevelPlanner from /home/nils/human_aware_rl/overcooked_ai/overcooked_ai_py/data/planners/simple_am.pkl


  0%|                                                                                             | 0/5 [00:00<?, ?it/s]

X X P X X 
O     ↑1O 
X ↑0    X 
X D X S X 

Found goal after: 	1.63 seconds,   	7797 state expanded (0.33 unique) 	 ~4788.31 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((3, 1), (1, 0)))
failures:  0
Timestep: 1
Joint action taken: ('↑', 'stay') 	 Reward: 0 + shape * 0 
X X P X X 
O ↑0  ↑1O 
X       X 
X D X S X 


Found goal after: 	1.58 seconds,   	7826 state expanded (0.32 unique) 	 ~4960.11 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 2
Joint action taken: ('←', 'stay') 	 Reward: 0 + shape * 0 
X X P X X 
O ←0  ↑1O 
X       X 
X D X S X 


Found goal after: 	1.85 seconds,   	7776 state expanded (0.33 unique) 	 ~4203.11 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((3, 1), (1, 0)))
failures:  0
Timestep: 3
Joint action taken: ('interact', 'stay') 	 Reward: 0 + shape * 0 
X X P X X 
O ←o  ↑1O 
X       X 
X D X S X 


Found goal after: 	1.66 seconds,   	7591 state expanded (0.32 unique) 	 ~4560.51 expansions/s
First m

Found goal after: 	0.80 seconds,   	3490 state expanded (0.33 unique) 	 ~4378.86 expansions/s
First motion goal:  (((3, 1), (1, 0)), ((1, 2), (0, 1)))
failures:  18
Timestep: 41
Joint action taken: ('interact', '←') 	 Reward: 0 + shape * 0 
X X ø20X X 
O     →oO 
X ←1    X 
X D XoS X 


Found goal after: 	0.79 seconds,   	3482 state expanded (0.33 unique) 	 ~4380.07 expansions/s
First motion goal:  (((3, 1), (1, 0)), ((1, 2), (0, 1)))
failures:  18
Timestep: 42
Joint action taken: ('interact', '↓') 	 Reward: 0 + shape * 0 
X X ø20X X 
O     →oO 
X ↓1    X 
X D XoS X 


Found goal after: 	0.80 seconds,   	3478 state expanded (0.33 unique) 	 ~4348.19 expansions/s
First motion goal:  (((3, 1), (1, 0)), ((1, 2), (0, 1)))
failures:  18
Timestep: 43
Joint action taken: ('interact', 'interact') 	 Reward: 0 + shape * 0 
X X ø20X X 
O     →oO 
X ↓d    X 
X D XoS X 


Found goal after: 	0.86 seconds,   	3461 state expanded (0.33 unique) 	 ~4027.55 expansions/s
First motion goal:  (((3, 1), (1, 0

Found goal after: 	1.31 seconds,   	5664 state expanded (0.33 unique) 	 ~4309.36 expansions/s
First motion goal:  (((1, 2), (0, 1)), ((1, 1), (-1, 0)))
failures:  18
Timestep: 70
Joint action taken: ('←', '↑') 	 Reward: 0 + shape * 0 
X X ø4X X 
O ↑1    O 
X ←0    X 
X D XoS X 


Found goal after: 	1.48 seconds,   	5378 state expanded (0.33 unique) 	 ~3625.31 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((1, 2), (0, 1)))
failures:  18
Timestep: 71
Joint action taken: ('↑', 'stay') 	 Reward: 0 + shape * 0 
X X ø5X X 
O ↑1    O 
X ↑0    X 
X D XoS X 


Found goal after: 	1.25 seconds,   	5317 state expanded (0.33 unique) 	 ~4249.19 expansions/s
First motion goal:  (((1, 2), (0, 1)), ((1, 1), (-1, 0)))
failures:  18
Timestep: 72
Joint action taken: ('↓', 'stay') 	 Reward: 0 + shape * 0 
X X ø6X X 
O ↑1    O 
X ↓0    X 
X D XoS X 


Found goal after: 	1.14 seconds,   	4888 state expanded (0.33 unique) 	 ~4294.06 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((1, 1), (-1, 0))

...

Found goal after: 	7.38 seconds,   	36429 state expanded (0.36 unique) 	 ~4933.63 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 2), (1, 0)))
failures:  0
Timestep: 48
Joint action taken: ('↑', 'stay') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X       P ↑0    X 
X     →oø20      X 
X X X D X D X X X 


Found goal after: 	4.99 seconds,   	21483 state expanded (0.37 unique) 	 ~4308.21 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 2), (1, 0)))
failures:  0
Timestep: 49
Joint action taken: ('interact', '↑') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X     ↑oP ↑o    X 
X       ø20      X 
X X X D X D X X X 


Found goal after: 	3.61 seconds,   	17572 state expanded (0.37 unique) 	 ~4869.15 expansions/s
First motion goal:  (((5, 2), (-1, 0)), ((3, 2), (1, 0)))
failures:  0
Timestep: 50
Joint action taken: ('←', 'stay') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X     ↑oP ←o    X 
X       ø20      X 
X X X D X

Found goal after: 	10.07 seconds,   	45224 state expanded (0.35 unique) 	 ~4489.81 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 3), (1, 0)))
failures:  0
Timestep: 73
Joint action taken: ('↑', 'stay') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X       ø15↑0    X 
X ↓o    P       X 
X X X D X D X X X 


Found goal after: 	8.92 seconds,   	41716 state expanded (0.35 unique) 	 ~4674.90 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 3), (1, 0)))
failures:  0
Timestep: 74
Joint action taken: ('interact', 'stay') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X       ø16↑o    X 
X ↓o    P       X 
X X X D X D X X X 


Found goal after: 	4.69 seconds,   	22511 state expanded (0.36 unique) 	 ~4798.22 expansions/s
First motion goal:  (((5, 3), (-1, 0)), ((3, 3), (1, 0)))
failures:  0
Timestep: 75
Joint action taken: ('↓', '↓') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X       ø17      X 
X ↓o    P ↓o    X 
X X X D 

100%|████████████████████████████████████████████████████████████████████████████████████| 5/5 [48:46<00:00, 585.36s/it]

Found goal after: 	0.01 seconds,   	37 state expanded (0.89 unique) 	 ~3458.49 expansions/s
First motion goal:  (((5, 2), (-1, 0)), ((3, 2), (1, 0)))
failures:  0
Timestep: 99
Joint action taken: ('interact', 'stay') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X     →dP ←s    X 
X       ø18      X 
X X X D X D X X X 


Found goal after: 	0.00 seconds,   	10 state expanded (1.00 unique) 	 ~4837.16 expansions/s
First motion goal:  (((7, 1), (1, 0)), ((3, 3), (1, 0)))
failures:  0
Timestep: 100
Joint action taken: ('→', 'stay') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X     →dP   →s  X 
X       ø19      X 
X X X D X D X X X 


Avg reward 40.00 (std: 0.00, se: 0.00) over 5 games of avg length 100.0


{'simple': 40.0, 'unident_s': 40.0}

In [7]:
# CP+HPROXY (switch indices) horizon 100, 5x
cp_performance = {}
for layout in layouts:
    ae = AgentEvaluator(mdp_params={'layout_name': layout}, env_params={'horizon': 100})
    
    test_model_name = best_bc_models["test"][layout]
    agent_bc_test, _ = get_bc_agent_from_saved(test_model_name)
    agent_bc_test.stochastic = False
    
    a0 = CoupledPlanningExperimentalAgent(ae.mlp)
    agent_pair = AgentPair(agent_bc_test, a0)
    
    traj = ae.evaluate_agent_pair(agent_pair, 5, display=display)
    cp_performance[layout] = traj['ep_returns'][0]

cp_performance

Loading a model without an environment, this model cannot be trained until it has a valid environment.
Loaded MediumLevelPlanner from /home/nils/human_aware_rl/overcooked_ai/overcooked_ai_py/data/planners/simple_am.pkl
Loaded MediumLevelPlanner from /home/nils/human_aware_rl/overcooked_ai/overcooked_ai_py/data/planners/simple_am.pkl


  0%|                                                                                             | 0/5 [00:00<?, ?it/s]

X X P X X 
O     ↑1O 
X ↑0    X 
X D X S X 

Found goal after: 	1.61 seconds,   	7797 state expanded (0.33 unique) 	 ~4837.62 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((3, 1), (1, 0)))
failures:  0
Timestep: 1
Joint action taken: ('stay', '→') 	 Reward: 0 + shape * 0 
X X P X X 
O     →1O 
X ↑0    X 
X D X S X 


Found goal after: 	1.81 seconds,   	7842 state expanded (0.32 unique) 	 ~4342.21 expansions/s
First motion goal:  (((1, 2), (0, 1)), ((3, 1), (1, 0)))
failures:  0
Timestep: 2
Joint action taken: ('stay', 'interact') 	 Reward: 0 + shape * 0 
X X P X X 
O     →oO 
X ↑0    X 
X D X S X 


Found goal after: 	1.81 seconds,   	7612 state expanded (0.32 unique) 	 ~4207.64 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((2, 1), (0, -1)))
failures:  0
Timestep: 3
Joint action taken: ('stay', '←') 	 Reward: 0 + shape * 0 
X X P X X 
O   ←o  O 
X ↑0    X 
X D X S X 


Found goal after: 	1.67 seconds,   	7702 state expanded (0.32 unique) 	 ~4611.94 expansions/s
First mo

Found goal after: 	0.78 seconds,   	3383 state expanded (0.33 unique) 	 ~4326.04 expansions/s
First motion goal:  (((2, 1), (0, -1)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 30
Joint action taken: ('↑', 'interact') 	 Reward: 0 + shape * 0 
X X ø14X X 
O ←o↑d  O 
X       X 
X D X S X 


Found goal after: 	0.83 seconds,   	3381 state expanded (0.33 unique) 	 ~4089.14 expansions/s
First motion goal:  (((2, 1), (0, -1)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 31
Joint action taken: ('stay', 'interact') 	 Reward: 0 + shape * 0 
X X ø15X X 
O ←o↑d  O 
X       X 
X D X S X 


Found goal after: 	0.80 seconds,   	3379 state expanded (0.33 unique) 	 ~4207.56 expansions/s
First motion goal:  (((2, 1), (0, -1)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 32
Joint action taken: ('stay', 'interact') 	 Reward: 0 + shape * 0 
X X ø16X X 
O ←o↑d  O 
X       X 
X D X S X 


Found goal after: 	0.73 seconds,   	3377 state expanded (0.33 unique) 	 ~4603.50 expansions/s
First motion goal:  (((2, 1), (0,

Found goal after: 	1.24 seconds,   	5617 state expanded (0.33 unique) 	 ~4536.55 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((1, 2), (0, 1)))
failures:  0
Timestep: 59
Joint action taken: ('stay', '→') 	 Reward: 0 + shape * 0 
X X ø3X X 
O   →1  O 
X ←0    X 
X D X S X 


Found goal after: 	1.17 seconds,   	5261 state expanded (0.33 unique) 	 ~4507.88 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((1, 2), (0, 1)))
failures:  0
Timestep: 60
Joint action taken: ('interact', '↓') 	 Reward: 0 + shape * 0 
X X ø4X X 
O       O 
X ←0↓1  X 
X D X S X 


Found goal after: 	1.03 seconds,   	5188 state expanded (0.33 unique) 	 ~5030.38 expansions/s
First motion goal:  (((1, 2), (0, 1)), ((3, 1), (1, 0)))
failures:  0
Timestep: 61
Joint action taken: ('↓', '↑') 	 Reward: 0 + shape * 0 
X X ø5X X 
O   ↑1  O 
X ↓0    X 
X D X S X 


Found goal after: 	1.15 seconds,   	5353 state expanded (0.33 unique) 	 ~4663.38 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((1, 2), (0, 1)))

...

Found goal after: 	0.58 seconds,   	3852 state expanded (0.37 unique) 	 ~6630.22 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 2), (1, 0)))
failures:  0
Timestep: 50
Joint action taken: ('interact', '→') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X     →dø6      X 
X       ø20↓d    X 
X X X D X D X X X 


Found goal after: 	0.28 seconds,   	2015 state expanded (0.35 unique) 	 ~7134.48 expansions/s
First motion goal:  (((5, 2), (-1, 0)), ((3, 2), (1, 0)))
failures:  0
Timestep: 51
Joint action taken: ('↑', 'interact') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X     →dø7↑d    X 
X       ø20      X 
X X X D X D X X X 


Found goal after: 	0.48 seconds,   	1716 state expanded (0.36 unique) 	 ~3572.43 expansions/s
First motion goal:  (((5, 2), (-1, 0)), ((3, 2), (1, 0)))
failures:  0
Timestep: 52
Joint action taken: ('stay', 'interact') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X     →dø8↑d    X 
X       ø20      X 
X

Found goal after: 	16.55 seconds,   	87961 state expanded (0.35 unique) 	 ~5316.16 expansions/s
First motion goal:  (((7, 1), (1, 0)), ((3, 2), (1, 0)))
failures:  0
Timestep: 75
Joint action taken: ('→', 'interact') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X     →1ø-    →sX 
X       P       X 
X X X D X D X X X 


Found goal after: 	8.10 seconds,   	44530 state expanded (0.35 unique) 	 ~5494.67 expansions/s
First motion goal:  (((7, 1), (1, 0)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 76
Joint action taken: ('↑', '←') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X ↑sS 
X   ←1  ø-      X 
X       P       X 
X X X D X D X X X 


Found goal after: 	8.57 seconds,   	47192 state expanded (0.35 unique) 	 ~5504.63 expansions/s
First motion goal:  (((7, 1), (1, 0)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 77
Joint action taken: ('→', '←') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X →sS 
X ←1    ø-      X 
X       P       X 
X X X D X D X X X 

100%|█████████████████████████████████████████████████████████████████████████████████| 5/5 [1:26:17<00:00, 1035.49s/it]

Found goal after: 	7.20 seconds,   	43723 state expanded (0.33 unique) 	 ~6074.23 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 3), (1, 0)))
failures:  0
Timestep: 100
Joint action taken: ('interact', '↓') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X       ø=↑o    X 
X     ↓oø-      X 
X X X D X D X X X 


Avg reward 40.00 (std: 0.00, se: 0.00) over 5 games of avg length 100.0


{'simple': 40.0, 'unident_s': 40.0}

In [8]:
# CP+HPROXY horizon 400, 5x
cp_performance = {}
for layout in layouts:
    ae = AgentEvaluator(mdp_params={'layout_name': layout}, env_params={'horizon': 400})
    
    test_model_name = best_bc_models["test"][layout]
    agent_bc_test, _ = get_bc_agent_from_saved(test_model_name)
    agent_bc_test.stochastic = False
    
    a0 = CoupledPlanningExperimentalAgent(ae.mlp)
    agent_pair = AgentPair(a0, agent_bc_test)
    
    traj = ae.evaluate_agent_pair(agent_pair, 5, display=display)
    cp_performance[layout] = traj['ep_returns'][0]

cp_performance

Loading a model without an environment, this model cannot be trained until it has a valid environment.
Loaded MediumLevelPlanner from /home/nils/human_aware_rl/overcooked_ai/overcooked_ai_py/data/planners/simple_am.pkl
Loaded MediumLevelPlanner from /home/nils/human_aware_rl/overcooked_ai/overcooked_ai_py/data/planners/simple_am.pkl


  0%|                                                                                             | 0/5 [00:00<?, ?it/s]

X X P X X 
O     ↑1O 
X ↑0    X 
X D X S X 

Found goal after: 	1.43 seconds,   	7797 state expanded (0.33 unique) 	 ~5462.99 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((3, 1), (1, 0)))
failures:  0
Timestep: 1
Joint action taken: ('↑', 'stay') 	 Reward: 0 + shape * 0 
X X P X X 
O ↑0  ↑1O 
X       X 
X D X S X 


Found goal after: 	1.46 seconds,   	7826 state expanded (0.32 unique) 	 ~5370.84 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 2
Joint action taken: ('←', 'stay') 	 Reward: 0 + shape * 0 
X X P X X 
O ←0  ↑1O 
X       X 
X D X S X 


Found goal after: 	1.47 seconds,   	7776 state expanded (0.33 unique) 	 ~5284.89 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((3, 1), (1, 0)))
failures:  0
Timestep: 3
Joint action taken: ('interact', 'stay') 	 Reward: 0 + shape * 0 
X X P X X 
O ←o  ↑1O 
X       X 
X D X S X 


Found goal after: 	1.43 seconds,   	7591 state expanded (0.32 unique) 	 ~5320.29 expansions/s
First m

Found goal after: 	0.71 seconds,   	3490 state expanded (0.33 unique) 	 ~4941.32 expansions/s
First motion goal:  (((3, 1), (1, 0)), ((1, 2), (0, 1)))
failures:  18
Timestep: 41
Joint action taken: ('interact', '←') 	 Reward: 0 + shape * 0 
X X ø20X X 
O     →oO 
X ←1    X 
X D XoS X 


Found goal after: 	0.67 seconds,   	3482 state expanded (0.33 unique) 	 ~5188.89 expansions/s
First motion goal:  (((3, 1), (1, 0)), ((1, 2), (0, 1)))
failures:  18
Timestep: 42
Joint action taken: ('interact', '↓') 	 Reward: 0 + shape * 0 
X X ø20X X 
O     →oO 
X ↓1    X 
X D XoS X 


Found goal after: 	0.70 seconds,   	3478 state expanded (0.33 unique) 	 ~4991.71 expansions/s
First motion goal:  (((3, 1), (1, 0)), ((1, 2), (0, 1)))
failures:  18
Timestep: 43
Joint action taken: ('interact', 'interact') 	 Reward: 0 + shape * 0 
X X ø20X X 
O     →oO 
X ↓d    X 
X D XoS X 


Found goal after: 	0.67 seconds,   	3461 state expanded (0.33 unique) 	 ~5142.94 expansions/s
First motion goal:  (((3, 1), (1, 0

Found goal after: 	1.02 seconds,   	5664 state expanded (0.33 unique) 	 ~5536.33 expansions/s
First motion goal:  (((1, 2), (0, 1)), ((1, 1), (-1, 0)))
failures:  18
Timestep: 70
Joint action taken: ('←', '↑') 	 Reward: 0 + shape * 0 
X X ø4X X 
O ↑1    O 
X ←0    X 
X D XoS X 


Found goal after: 	0.96 seconds,   	5378 state expanded (0.33 unique) 	 ~5610.09 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((1, 2), (0, 1)))
failures:  18
Timestep: 71
Joint action taken: ('↑', 'stay') 	 Reward: 0 + shape * 0 
X X ø5X X 
O ↑1    O 
X ↑0    X 
X D XoS X 


Found goal after: 	1.03 seconds,   	5317 state expanded (0.33 unique) 	 ~5144.16 expansions/s
First motion goal:  (((1, 2), (0, 1)), ((1, 1), (-1, 0)))
failures:  18
Timestep: 72
Joint action taken: ('↓', 'stay') 	 Reward: 0 + shape * 0 
X X ø6X X 
O ↑1    O 
X ↓0    X 
X D XoS X 


Found goal after: 	0.91 seconds,   	4888 state expanded (0.33 unique) 	 ~5366.23 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((1, 1), (-1, 0))

...

Found goal after: 	0.02 seconds,   	86 state expanded (0.80 unique) 	 ~3584.63 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 2), (0, -1)))
failures:  0
Timestep: 355
Joint action taken: ('↑', 'interact') 	 Reward: 20 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
Xd    ↑1ø-↑0    X 
X       ø20      X 
X X X D X D X X X 


Found goal after: 	8.24 seconds,   	44890 state expanded (0.36 unique) 	 ~5445.02 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 356
Joint action taken: ('interact', '↓') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
Xd      ø-↑o    X 
X     ↓1ø20      X 
X X X D X D X X X 


Found goal after: 	7.14 seconds,   	40670 state expanded (0.36 unique) 	 ~5694.10 expansions/s
First motion goal:  (((5, 2), (-1, 0)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 357
Joint action taken: ('←', 'interact') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
Xd      ø-←o    X 
X     ↓dø20      

Found goal after: 	1.51 seconds,   	9940 state expanded (0.34 unique) 	 ~6597.19 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 3), (1, 0)))
failures:  0
Timestep: 380
Joint action taken: ('↑', 'interact') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
Xd    →dø19↑0    X 
X       ø2      X 
X X X D X D X X X 


Found goal after: 	1.40 seconds,   	9381 state expanded (0.34 unique) 	 ~6679.05 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 2), (1, 0)))
failures:  0
Timestep: 381
Joint action taken: ('interact', '→') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
Xd    →dø20↑o    X 
X       ø3      X 
X X X D X D X X X 


Found goal after: 	0.89 seconds,   	5464 state expanded (0.36 unique) 	 ~6173.09 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 3), (1, 0)))
failures:  0
Timestep: 382
Joint action taken: ('interact', '↓') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
Xd      ø20↑o    X 
X     ↓dø4      X 
X

100%|█████████████████████████████████████████████████████████████████████████████████| 5/5 [2:11:57<00:00, 1583.60s/it]

Timestep: 393
Joint action taken: ('interact', 'stay') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
Xd    ↑dø20↑o    X 
X       ø15      X 
X X X D X D X X X 


Found goal after: 	0.02 seconds,   	90 state expanded (0.58 unique) 	 ~4411.75 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 2), (1, 0)))
failures:  0
Timestep: 394
Joint action taken: ('interact', 'stay') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
Xd    ↑dø20↑o    X 
X       ø16      X 
X X X D X D X X X 


Found goal after: 	0.02 seconds,   	75 state expanded (0.64 unique) 	 ~4154.53 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 2), (1, 0)))
failures:  0
Timestep: 395
Joint action taken: ('interact', 'stay') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
Xd    ↑dø20↑o    X 
X       ø17      X 
X X X D X D X X X 


Found goal after: 	0.02 seconds,   	73 state expanded (0.74 unique) 	 ~3718.49 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 

{'simple': 180.0, 'unident_s': 280.0}

In [9]:
# CP+HPROXY (switch indices) horizon 400, 5x
cp_performance = {}
for layout in layouts:
    ae = AgentEvaluator(mdp_params={'layout_name': layout}, env_params={'horizon': 400})
    
    test_model_name = best_bc_models["test"][layout]
    agent_bc_test, _ = get_bc_agent_from_saved(test_model_name)
    agent_bc_test.stochastic = False
    
    a0 = CoupledPlanningExperimentalAgent(ae.mlp)
    agent_pair = AgentPair(agent_bc_test, a0)
    
    traj = ae.evaluate_agent_pair(agent_pair, 5, display=display)
    cp_performance[layout] = traj['ep_returns'][0]

cp_performance

Loading a model without an environment, this model cannot be trained until it has a valid environment.
Loaded MediumLevelPlanner from /home/nils/human_aware_rl/overcooked_ai/overcooked_ai_py/data/planners/simple_am.pkl
Loaded MediumLevelPlanner from /home/nils/human_aware_rl/overcooked_ai/overcooked_ai_py/data/planners/simple_am.pkl


  0%|                                                                                             | 0/5 [00:00<?, ?it/s]

X X P X X 
O     ↑1O 
X ↑0    X 
X D X S X 

Found goal after: 	1.38 seconds,   	7797 state expanded (0.33 unique) 	 ~5658.23 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((3, 1), (1, 0)))
failures:  0
Timestep: 1
Joint action taken: ('stay', '→') 	 Reward: 0 + shape * 0 
X X P X X 
O     →1O 
X ↑0    X 
X D X S X 


Found goal after: 	1.41 seconds,   	7842 state expanded (0.32 unique) 	 ~5571.30 expansions/s
First motion goal:  (((1, 2), (0, 1)), ((3, 1), (1, 0)))
failures:  0
Timestep: 2
Joint action taken: ('stay', 'interact') 	 Reward: 0 + shape * 0 
X X P X X 
O     →oO 
X ↑0    X 
X D X S X 


Found goal after: 	1.34 seconds,   	7612 state expanded (0.32 unique) 	 ~5663.79 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((2, 1), (0, -1)))
failures:  0
Timestep: 3
Joint action taken: ('stay', '←') 	 Reward: 0 + shape * 0 
X X P X X 
O   ←o  O 
X ↑0    X 
X D X S X 


Found goal after: 	1.37 seconds,   	7702 state expanded (0.32 unique) 	 ~5629.60 expansions/s
First mo

Found goal after: 	0.61 seconds,   	3383 state expanded (0.33 unique) 	 ~5583.09 expansions/s
First motion goal:  (((2, 1), (0, -1)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 30
Joint action taken: ('↑', 'interact') 	 Reward: 0 + shape * 0 
X X ø14X X 
O ←o↑d  O 
X       X 
X D X S X 


Found goal after: 	0.61 seconds,   	3381 state expanded (0.33 unique) 	 ~5565.30 expansions/s
First motion goal:  (((2, 1), (0, -1)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 31
Joint action taken: ('stay', 'interact') 	 Reward: 0 + shape * 0 
X X ø15X X 
O ←o↑d  O 
X       X 
X D X S X 


Found goal after: 	0.64 seconds,   	3379 state expanded (0.33 unique) 	 ~5310.78 expansions/s
First motion goal:  (((2, 1), (0, -1)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 32
Joint action taken: ('stay', 'interact') 	 Reward: 0 + shape * 0 
X X ø16X X 
O ←o↑d  O 
X       X 
X D X S X 


Found goal after: 	0.58 seconds,   	3377 state expanded (0.33 unique) 	 ~5830.13 expansions/s
First motion goal:  (((2, 1), (0,

Found goal after: 	1.02 seconds,   	5617 state expanded (0.33 unique) 	 ~5480.73 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((1, 2), (0, 1)))
failures:  0
Timestep: 59
Joint action taken: ('stay', '→') 	 Reward: 0 + shape * 0 
X X ø3X X 
O   →1  O 
X ←0    X 
X D X S X 


Found goal after: 	0.89 seconds,   	5261 state expanded (0.33 unique) 	 ~5940.60 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((1, 2), (0, 1)))
failures:  0
Timestep: 60
Joint action taken: ('interact', '↓') 	 Reward: 0 + shape * 0 
X X ø4X X 
O       O 
X ←0↓1  X 
X D X S X 


Found goal after: 	0.92 seconds,   	5188 state expanded (0.33 unique) 	 ~5668.28 expansions/s
First motion goal:  (((1, 2), (0, 1)), ((3, 1), (1, 0)))
failures:  0
Timestep: 61
Joint action taken: ('↓', '↑') 	 Reward: 0 + shape * 0 
X X ø5X X 
O   ↑1  O 
X ↓0    X 
X D X S X 


Found goal after: 	1.00 seconds,   	5353 state expanded (0.33 unique) 	 ~5368.20 expansions/s
First motion goal:  (((1, 1), (-1, 0)), ((1, 2), (0, 1)))

...

Found goal after: 	13.09 seconds,   	43723 state expanded (0.33 unique) 	 ~3340.78 expansions/s
First motion goal:  (((5, 2), (0, -1)), ((3, 3), (1, 0)))
failures:  0
Timestep: 368
Joint action taken: ('interact', '↓') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X       ø=↑o    X 
X     ↓oø-      X 
X X X D X D X X X 


Found goal after: 	9.64 seconds,   	34334 state expanded (0.32 unique) 	 ~3560.70 expansions/s
First motion goal:  (((5, 2), (-1, 0)), ((3, 2), (1, 0)))
failures:  0
Timestep: 369
Joint action taken: ('←', '↑') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X     ↑oø=←o    X 
X       ø-      X 
X X X D X D X X X 


Found goal after: 	6.21 seconds,   	21216 state expanded (0.33 unique) 	 ~3418.83 expansions/s
First motion goal:  (((5, 2), (-1, 0)), ((3, 2), (1, 0)))
failures:  0
Timestep: 370
Joint action taken: ('interact', '→') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X     →oø1←0    X 
X       ø-      X 
X X X D

Found goal after: 	0.62 seconds,   	2389 state expanded (0.39 unique) 	 ~3823.48 expansions/s
First motion goal:  (((5, 3), (-1, 0)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 393
Joint action taken: ('stay', '↑') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X     ↑1ø20↑d    X 
X       ø7      X 
X X X D X D X X X 


Found goal after: 	0.51 seconds,   	1952 state expanded (0.39 unique) 	 ~3863.03 expansions/s
First motion goal:  (((5, 2), (-1, 0)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 394
Joint action taken: ('stay', '←') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X   ←1  ø20↑d    X 
X       ø8      X 
X X X D X D X X X 


Found goal after: 	0.39 seconds,   	1280 state expanded (0.43 unique) 	 ~3265.32 expansions/s
First motion goal:  (((5, 2), (-1, 0)), ((3, 3), (0, 1)))
failures:  0
Timestep: 395
Joint action taken: ('←', '→') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X     →1ø20←d    X 
X       ø9      X 
X X X D X D X 

100%|█████████████████████████████████████████████████████████████████████████████████| 5/5 [5:22:52<00:00, 3874.44s/it]

Found goal after: 	0.15 seconds,   	492 state expanded (0.51 unique) 	 ~3357.67 expansions/s
First motion goal:  (((5, 2), (-1, 0)), ((1, 1), (-1, 0)))
failures:  0
Timestep: 399
Joint action taken: ('interact', '↑') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X     ↑1P ←s    X 
X       ø13      X 
X X X D X D X X X 


Found goal after: 	0.01 seconds,   	35 state expanded (0.54 unique) 	 ~3955.72 expansions/s
First motion goal:  (((7, 1), (1, 0)), ((3, 3), (0, 1)))
failures:  0
Timestep: 400
Joint action taken: ('→', '↓') 	 Reward: 0 + shape * 0 
X X X X X X X X X 
O   X S X O X   S 
X       P   →s  X 
X     ↓1ø14      X 
X X X D X D X X X 


Avg reward 200.00 (std: 0.00, se: 0.00) over 5 games of avg length 400.0


{'simple': 160.0, 'unident_s': 200.0}

Conclusions over num_games=5 :

CP + HProxy (BC_TEST)

100 horizon 

simple : 40 - failures 90/500 (5x)
unidents: 40 - failures 0 (5x)

400 horizon

simple : 180 - failures 90/2000 (5x)
unidents: 280 - failures 0 (5x)

Switched indices CP + HProxy (BC_TEST)

100 horizon -> extrapolate 400

simple : 40 - failures 0 (5x)
unidents: 40 - failres 0 (5x)

400 horizon

simple : 160 - failures 0 (5x)
unidents: 200 - failures 0 (5x)